In [1]:
from __future__ import division
import os, sys, re, json, time, datetime, shutil
import itertools, collections
from importlib import reload
from IPython.display import display, HTML
import tensorflow as tf


import nltk
nltk.download('wordnet')

from common import patched_numpy_io


from __future__ import print_function
from __future__ import division
import collections
import nltk
import numpy as np
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.model_selection import train_test_split
from nltk.tokenize.treebank import TreebankWordTokenizer
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import CountVectorizer

from sklearn.feature_extraction.text import TfidfTransformer

# Helper libraries
from common import utils, vocabulary

/home/younusahmed23/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


[nltk_data] Downloading package wordnet to
[nltk_data]     /home/younusahmed23/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [2]:
df = pd.read_csv('az_reduced_reviews.csv')

In [3]:
df.columns

Index(['business_id', 'stars', 'text'], dtype='object')

In [ ]:
biz_ids=df.groupby('business_id')
x=0
bizids={}
for name,group in biz_ids:
    #Processing restaurants that had more than three reviews. Number is up for debate.
    if len(group)>3:
        x+=1
        bizname="train_id_"+str(x)
        #This dictionary maps train_ids variables to business id. Just search bizids[train_id_1]=business_id
        bizids[bizname]=name
        count_vect = CountVectorizer(stop_words='english')
        X_train_counts = count_vect.fit_transform(group['text'])
        tfidf_transformer = TfidfTransformer()
        exec(bizname+'=tfidf_transformer.fit_transform(X_train_counts)')

In [ ]:
train_id_6

In [ ]:
df['text'][0]

# Importing Glove Vectors to use with Neural BOW

In [23]:
from GloveVectors import glove_helper; reload(glove_helper)

hands = glove_helper.Hands(ndim=300)  # 50, 100, 200, 300 dim are available"

Loading vectors from data/glove/glove.6B.zip
Parsing file: data/glove/glove.6B.zip:glove.6B.300d.txt
Found 400,000 words.
Parsing vectors... Done! (W.shape = (400003, 300))


In [3]:

import boto
import gensim

from gensim.parsing import PorterStemmer
global_stemmer = PorterStemmer()
 
class StemmingHelper(object):
    """
    Class to aid the stemming process - from word to stemmed form,
    and vice versa.
    The 'original' form of a stemmed word will be returned as the
    form in which its been used the most number of times in the text.
    """
 
    #This reverse lookup will remember the original forms of the stemmed
    #words
    word_lookup = {}
 
    @classmethod
    def stem(cls, word):
        """
        Stems a word and updates the reverse lookup.
        """
 
        #Stem the word
        stemmed = global_stemmer.stem(word)
 
        #Update the word lookup
        if stemmed not in cls.word_lookup:
            cls.word_lookup[stemmed] = {}
        cls.word_lookup[stemmed][word] = (
            cls.word_lookup[stemmed].get(word, 0) + 1)
 
        return stemmed
 
    @classmethod
    def original_form(cls, word):
        """
        Returns original form of a word given the stemmed version,
        as stored in the word lookup.
        """
 
        if word in cls.word_lookup:
            return max(cls.word_lookup[word].keys(),
                       key=lambda x: cls.word_lookup[word][x])
        else:
            return word
        
from gensim.models import Word2Vec
min_count = 2
size = 300
window = 10
 
# model = Word2Vec(sentences, min_count=min_count, size=size, window=window)

In [4]:
from gensim.models import KeyedVectors
filename = 'GoogleNews-vectors-negative300.bin'
model2vec = KeyedVectors.load_word2vec_format(filename, binary=True)

In [5]:
#Split the data
x_df = df[df.stars != 3]
#ignore warning
x_df['binary_stars'] =  np.where(x_df['stars'] >= 4, 1, 0)
X_train, X_test, y_train, y_test = train_test_split(x_df.text, x_df.binary_stars, test_size=0.20, random_state=42)

/home/younusahmed23/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  after removing the cwd from sys.path.


In [43]:
tokenizer = TreebankWordTokenizer()


In [24]:
def canonicalize(x):
    return utils.canonicalize_words(x,wordset=hands.vocab.wordset)
#     return utils.canonicalize_words(x,wordset=set(model2vec.vocab))

In [8]:
def double(x,wordset=None):
   g=[]
   bad=[]
   for y in x:
       if len(y)>1 and "." not in y and y in wordset:
            bad.append(y)
            try:
                g.append(hands.get_vector(y.strip('.')))
            except:
                print(y)
#    return [hands.vocab.word_to_id[y.strip('.')] for y in x if len(y)>1]
   return np.mean(g,axis=0)

   

In [9]:
def TFIDFembedding(x,wordset=None,TFIDFmatrix=None):
   g=[]
   bad=[]
   weights=[]
   for y in x:
       if len(y)>1 and "." not in y and y in wordset:
            bad.append(y)
            try:
                g.append(hands.get_vector(y.strip('.')))
                weights.append(TFIDFmatrix.loc[y].weight)
            except:
                print(y)
   
   temp=np.array([weight*vector for weight,vector in zip(weights,g)] )
   return np.sum(temp,axis=0)/np.sum(np.array(weights))

   

In [10]:
lemmatizer=WordNetLemmatizer()
def lemmatize(x):
    return lemmatizer.lemmatize(x)

# Training a Neural Network

In [11]:
TF_SAVEDIR = "/tmp/w266/yelp_model"
checkpoint_filename = os.path.join(TF_SAVEDIR, "NeuralBOW")
trained_filename = os.path.join(TF_SAVEDIR, "Final_Neural_BOW_Trained")

In [12]:
vocab=CountVectorizer(stop_words='english', min_df=5, max_df=0.75, ngram_range=(1, 1))
cvec=vocab.fit_transform(X_train)

In [13]:
TFIDF=TfidfTransformer()
TFIDFtransformed=TFIDF.fit_transform(cvec)
weights=np.asarray(TFIDFtransformed.mean(axis=0)).ravel().tolist()
weights_df=pd.DataFrame({'term':vocab.get_feature_names(),'weight':TFIDF.idf_})
weights_df.set_index('term',inplace=True)

In [14]:
batchreview=pd.DataFrame(X_train[0:50])['text']
tokens=batchreview.map(tokenizer.tokenize).map(canonicalize)
words=set(vocab.get_feature_names())
inp = pd.DataFrame(tokens.values)[0].map(lambda x:double(x,wordset=words))
# inp=token_ids.map(lambda x: [hands.get_vector(y) for y in x])

pf
generic
asian
say
min
wait
blinds
place
table
bathroom
service
manager
duty
sucker
charming
places
perfect
place
date
girls
lunch
dinner
live
work
near
ca
believe
did
try
spring
restaurant
week
loved
loved
loved
salad
filet
mignon
glazed
delicate
wine
port
sauce
good
ate
bite
super
picky
salads
best
creme
brulee
dessert
did
love
looked
menu
recently
wanting
come
items
appear
guess
special
restaurant
kind
bummer
definitely
wo
stop
charming
atmosphere
delish
dinner
option
place
written
review
yelp
having
boneless
wings
couple
years
ago
little
salty
decided
try
live
amazing
food
past
completely
tj
great
server
nice
fake
fiancé
place
knows
love
try
new
places
satisfy
food
friend
state
came
visit
decided
bring
time
experience
coffee
food
general
ordered
mexican
benedict
flight
coffee
iced
food
expected
chorizo
tasty
right
taste
buds
time
poached
eggs
loved
great
taste
just
mouth
did
realize
ordered
flight
iced
coffee
iced
latte
definitely
left
coffee
place
bring
fiancé
brunch
kind
pricey

/home/younusahmed23/anaconda3/lib/python3.6/site-packages/numpy/core/fromnumeric.py:2957: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/home/younusahmed23/anaconda3/lib/python3.6/site-packages/numpy/core/_methods.py:80: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


# Neural Network with Lemmatization

In [12]:
from GloveVectors import models; reload(models)

x, y = X_train, y_train
batch_size = 50

#Use Countvectorizer to utilize its built in stop word feature and min document frequency functionality

# vocab=CountVectorizer(stop_words='english', min_df=5, ngram_range=(1, 1))
# vocab.fit_transform(X_train)
# words=vocab.get_feature_names()


# Specify model hyperparameters as used by model_fn


model_params = dict(V=hands.vocab.size, embed_dim=300, hidden_dims=[300,150,75], num_classes=2,
                    encoder_type='bow',
                    lr=0.01, optimizer='adam', beta=0.01,dropout_rate=0.01)
model_fn = models.classifier_model_fn

#STORING TEST DATA INTO ITS OWN VARIABLE

testx, testy = X_test, y_test

testreview=pd.DataFrame(testx)['text']
tokens=testreview.map(tokenizer.tokenize).map(canonicalize)
temp=pd.DataFrame(tokens)['text'].map(lambda x:[lemmatize(y) for y in x])
inp = pd.DataFrame(temp.values)[0].map(lambda x:double(x,wordset=words))


inp_no_nans=pd.DataFrame({'col1':inp.values,'col2':testy}).dropna()

test_input_fn =  tf.estimator.inputs.numpy_input_fn(
              x={"ids": np.vstack(inp_no_nans.col1.values)},
    y=np.squeeze(pd.DataFrame(inp_no_nans.col2).values),shuffle=False)


    
# RUNNING NEURAL NETWORK


# Clear old log directory
shutil.rmtree(TF_SAVEDIR, ignore_errors=True)

if not os.path.isdir(TF_SAVEDIR):
    os.makedirs(TF_SAVEDIR)
    
with tf.Graph().as_default(), tf.Session() as sess:
    ##
    # Construct the graph here. No session.run calls - just wiring up Tensors.
    ##
    # Add placeholders so we can feed in data.
    x_ph_  = tf.placeholder(tf.float32, shape=[None,model_params['embed_dim']])  # [batch_size x embedding size]
    y_ph_  = tf.placeholder(tf.int32, shape=[None])              # [batch_size]
    
    # Construct the graph using model_fn
    features = {"ids": x_ph_,"hands":hands}  # note that values are Tensors
    estimator_spec = model_fn(features, labels=y_ph_, mode=tf.estimator.ModeKeys.TRAIN,
                              params=model_params)
    loss_     = estimator_spec.loss
    train_op_ = estimator_spec.train_op
    
    ##
    # Done constructing the graph, now we can make session.run calls.
    ##
    sess.run(tf.global_variables_initializer())
    saver = tf.train.Saver()
    
    # Run a single epoch
    t0 = time.time()
    model = tf.estimator.Estimator(model_fn=models.classifier_model_fn, 
           params=model_params,model_dir=trained_filename
           )
    iter=0
    for (bx, by) in utils.multi_batch_generator(100000, x, y):
        # feed NumPy arrays into the placeholder Tensors
        batchreview=pd.DataFrame(bx)['text']
        tokens=batchreview.map(tokenizer.tokenize).map(canonicalize)
        temp=pd.DataFrame(tokens)['text'].map(lambda x:[lemmatize(y) for y in x])
        inp = pd.DataFrame(temp.values)[0].map(lambda x:double(x,wordset=words))
        try:
#             feed_dict = {x_ph_: np.vstack(inp), y_ph_: by}
#             batch_loss, _ = sess.run([loss_, train_op_], feed_dict=feed_dict)

            train_input_fn = tf.estimator.inputs.numpy_input_fn(
                            x={"ids": np.vstack(inp)}, y=np.squeeze(pd.DataFrame(by).values),
                            batch_size=batch_size, num_epochs=1, shuffle=False)
            model.train(input_fn=train_input_fn)
            iter+=1
            if iter%1==0:
#                 model.evaluate(input_fn=train_input_fn)
                saver.save(sess, checkpoint_filename, global_step=iter)
                eval_metrics = model.evaluate(input_fn=test_input_fn, name="test")
                print("Accuracy on test set: {:.02%}".format(eval_metrics['accuracy']))
                print("Recall on test set: {:.02%}".format(eval_metrics['recall']))
                print("precision on test set: {:.02%}".format(eval_metrics['precision']))
#                 print("F1 Score on test set: {:.02%}".format(2*eval_metrics['precision']*eval_metrics['recall']/(eval_metrics['precision']+eval_metrics['recall'])))
                eval_metrics
        except:
            continue
#             saver.save(sess, checkpoint_filename, global_step=epoch)
        
  
    print("Completed one epoch in {:s}".format(utils.pretty_timedelta(since=t0)))
    saver.save(sess, trained_filename)
    
    
    
    #### EVALUATE TEST DATA BELOW###

    testx, testy = X_test, y_test

    testreview=pd.DataFrame(testx)['text']
    tokens=testreview.map(tokenizer.tokenize).map(canonicalize)
    temp=pd.DataFrame(tokens)['text'].map(lambda x:[lemmatize(y) for y in x])
    inp = pd.DataFrame(temp.values)[0].map(lambda x:double(x,wordset=words))
    
    
    inp_no_nans=pd.DataFrame({'col1':inp.values,'col2':testy}).dropna()

    test_input_fn =  tf.estimator.inputs.numpy_input_fn(
                  x={"ids": np.vstack(inp_no_nans.col1.values)},
        y=np.squeeze(pd.DataFrame(inp_no_nans.col2).values),shuffle=False)


    eval_metrics = model.evaluate(input_fn=test_input_fn, name="test")
    print("Accuracy on test set: {:.02%}".format(eval_metrics['accuracy']))
    print("Recall on test set: {:.02%}".format(eval_metrics['recall']))
    print("precision on test set: {:.02%}".format(eval_metrics['precision']))
#     print("F1 Score on test set: {:.02%}".format(2*eval_metrics['precision']*eval_metrics['recall']/(eval_metrics['precision']+eval_metrics['recall'])))
    eval_metrics

profiterole
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
tastebud
smoothy
tastebud
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
tastebud


/home/younusahmed23/anaconda3/lib/python3.6/site-packages/numpy/core/fromnumeric.py:2957: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/home/younusahmed23/anaconda3/lib/python3.6/site-packages/numpy/core/_methods.py:80: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


smoothy
smoothy
tastebud
tastebud
tastebud
smoothy
tastebud
smoothy
tablemate
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
profiterole
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
tastebud
profiterole
tablemate
smoothy
profiterole
profiterole
smoothy
smoothy
profiterole
smoothy
tastebud
profiterole
smoothy
tastebud
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
tastebud
smoothy
smoothy
smoothy
tastebud
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
sm

INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 7 into /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt.
INFO:tensorflow:loss = 22.736814, step = 7
INFO:tensorflow:Loss for final step: 22.736814.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt-7
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 8 into /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt.
INFO:tensorflow:loss = 26.12653, step = 8
INFO:tensorflow:Loss for final step: 26.12653.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters 

INFO:tensorflow:loss = 14.399996, step = 22
INFO:tensorflow:Loss for final step: 14.399996.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt-22
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 23 into /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt.
INFO:tensorflow:loss = 19.98254, step = 23
INFO:tensorflow:Loss for final step: 19.98254.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt-23
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints 

...

INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 12872 into /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt.
INFO:tensorflow:loss = 10.705214, step = 12872
INFO:tensorflow:Loss for final step: 10.705214.
smoothy
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt-12872
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 12873 into /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt.
INFO:tensorflow:loss = 10.230656, step = 12873
INFO:tensorflow:Loss for final step: 10.230656.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp

INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 12887 into /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt.
INFO:tensorflow:loss = 8.274587, step = 12887
INFO:tensorflow:Loss for final step: 8.274587.
smoothy
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt-12887
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 12888 into /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt.
INFO:tensorflow:loss = 17.264977, step = 12888
INFO:tensorflow:Loss for final step: 17.264977.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/w

INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 12901 into /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt.
INFO:tensorflow:loss = 7.847954, step = 12901
INFO:tensorflow:Loss for final step: 7.847954.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt-12901
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 12902 into /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt.
INFO:tensorflow:loss = 23.32118, step = 12902
INFO:tensorflow:Loss for final step: 23.32118.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Res

INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 12916 into /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt.
INFO:tensorflow:loss = 12.210948, step = 12916
INFO:tensorflow:Loss for final step: 12.210948.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt-12916
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 12917 into /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt.
INFO:tensorflow:loss = 11.7573, step = 12917
INFO:tensorflow:Loss for final step: 11.7573.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/w266/yelp_m

smoothy
smoothy
smoothy
smoothy
smoothy
profiterole
smoothy
tastebud
smoothy
smoothy
tastebud
tastebud
tastebud
smoothy
tastebud
tastebud
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
tastebud
smoothy
tastebud
smoothy
smoothy
smoothy
tastebud
smoothy
tastebud
smoothy
tastebud
smoothy
smoothy
tastebud
smoothy
tablemate
smoothy
smoothy
tastebud
tastebud
tastebud
smoothy
tastebud
smoothy
tastebud
smoothy
tastebud
smoothy
smoothy
tastebud
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
tastebud
tastebud
profiterole
tastebud
tastebud
smoothy
smoothy
smoothy
tastebud
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoo

# Neural Network with Lemmatization plus TF IDF

In [80]:
from GloveVectors import models; reload(models)

x, y = X_train, y_train
batch_size = 50

#Use Countvectorizer to utilize its built in stop word feature and min document frequency functionality

# vocab=CountVectorizer(stop_words='english', min_df=5, ngram_range=(1, 1))
# vocab.fit_transform(X_train)
# words=vocab.get_feature_names()


# Specify model hyperparameters as used by model_fn


model_params = dict(V=hands.vocab.size, embed_dim=300, hidden_dims=[300,150,75], num_classes=2,
                    encoder_type='bow',
                    lr=0.01, optimizer='adam', beta=0.01,dropout_rate=0.01)
model_fn = models.classifier_model_fn

#STORING TEST DATA INTO ITS OWN VARIABLE

testx, testy = X_test, y_test

testreview=pd.DataFrame(testx)['text']
tokens=testreview.map(tokenizer.tokenize).map(canonicalize)
temp=pd.DataFrame(tokens)['text'].map(lambda x:[lemmatize(y) for y in x])
inp = pd.DataFrame(temp.values)[0].map(lambda x:TFIDFembedding(x,wordset=words,TFIDFmatrix=weights_df))


inp_no_nans=pd.DataFrame({'col1':inp.values,'col2':testy}).dropna()

test_input_fn =  tf.estimator.inputs.numpy_input_fn(
              x={"ids": np.vstack(inp_no_nans.col1.values)},
    y=np.squeeze(pd.DataFrame(inp_no_nans.col2).values),shuffle=False)


    
# RUNNING NEURAL NETWORK


# Clear old log directory
shutil.rmtree(TF_SAVEDIR, ignore_errors=True)

if not os.path.isdir(TF_SAVEDIR):
    os.makedirs(TF_SAVEDIR)
    
with tf.Graph().as_default(), tf.Session() as sess:
    ##
    # Construct the graph here. No session.run calls - just wiring up Tensors.
    ##
    # Add placeholders so we can feed in data.
    x_ph_  = tf.placeholder(tf.float32, shape=[None,model_params['embed_dim']])  # [batch_size x embedding size]
    y_ph_  = tf.placeholder(tf.int32, shape=[None])              # [batch_size]
    
    # Construct the graph using model_fn
    features = {"ids": x_ph_,"hands":hands}  # note that values are Tensors
    estimator_spec = model_fn(features, labels=y_ph_, mode=tf.estimator.ModeKeys.TRAIN,
                              params=model_params)
    loss_     = estimator_spec.loss
    train_op_ = estimator_spec.train_op
    
    ##
    # Done constructing the graph, now we can make session.run calls.
    ##
    sess.run(tf.global_variables_initializer())
    saver = tf.train.Saver()
    
    # Run a single epoch
    t0 = time.time()
    model = tf.estimator.Estimator(model_fn=models.classifier_model_fn, 
           params=model_params,model_dir=trained_filename
           )
    iter=0
    for (bx, by) in utils.multi_batch_generator(100000, x, y):
        # feed NumPy arrays into the placeholder Tensors
        batchreview=pd.DataFrame(bx)['text']
        tokens=batchreview.map(tokenizer.tokenize).map(canonicalize)
        temp=pd.DataFrame(tokens)['text'].map(lambda x:[lemmatize(y) for y in x])
        inp = pd.DataFrame(temp.values)[0].map(lambda x:TFIDFembedding(x,wordset=words,TFIDFmatrix=weights_df))

        inp_no_nans=pd.DataFrame({'col1':inp.values,'col2':by}).dropna()

        train_input_fn = tf.estimator.inputs.numpy_input_fn(
                        x={"ids":  np.vstack(inp_no_nans.col1.values)},
                        y=np.squeeze(pd.DataFrame(inp_no_nans.col2).values),
                        batch_size=batch_size, num_epochs=1, shuffle=False)
        model.train(input_fn=train_input_fn)
        iter+=1
        if iter%1==0:
#                 model.evaluate(input_fn=train_input_fn)
            saver.save(sess, checkpoint_filename, global_step=iter)
            eval_metrics = model.evaluate(input_fn=test_input_fn, name="test")
            print("Accuracy on test set: {:.02%}".format(eval_metrics['accuracy']))
            print("Recall on test set: {:.02%}".format(eval_metrics['recall']))
            print("precision on test set: {:.02%}".format(eval_metrics['precision']))
#                 print("F1 Score on test set: {:.02%}".format(2*eval_metrics['precision']*eval_metrics['recall']/(eval_metrics['precision']+eval_metrics['recall'])))
            eval_metrics
            predictions=model.predict(input_fn=test_input_fn)

        
  
    print("Completed one epoch in {:s}".format(utils.pretty_timedelta(since=t0)))
    saver.save(sess, trained_filename)
    
    
    
    #### EVALUATE TEST DATA BELOW###

    testx, testy = X_test, y_test

    testreview=pd.DataFrame(testx)['text']
    tokens=testreview.map(tokenizer.tokenize).map(canonicalize)
    temp=pd.DataFrame(tokens)['text'].map(lambda x:[lemmatize(y) for y in x])
    inp = pd.DataFrame(temp.values)[0].map(lambda x:TFIDFembedding(x,wordset=words,TFIDFmatrix=weights_df))
    
    
    inp_no_nans=pd.DataFrame({'col1':inp.values,'col2':testy}).dropna()

    test_input_fn =  tf.estimator.inputs.numpy_input_fn(
                  x={"ids": np.vstack(inp_no_nans.col1.values)},
        y=np.squeeze(pd.DataFrame(inp_no_nans.col2).values),shuffle=False)


    eval_metrics = model.evaluate(input_fn=test_input_fn, name="test")
    print("Accuracy on test set: {:.02%}".format(eval_metrics['accuracy']))
    print("Recall on test set: {:.02%}".format(eval_metrics['recall']))
    print("precision on test set: {:.02%}".format(eval_metrics['precision']))
#     print("F1 Score on test set: {:.02%}".format(2*eval_metrics['precision']*eval_metrics['recall']/(eval_metrics['precision']+eval_metrics['recall'])))
    eval_metrics
    predictions=model.predict(input_fn=test_input_fn)

profiterole
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
tastebud
smoothy
tastebud
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy


/home/younusahmed23/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:15: RuntimeWarning: invalid value encountered in double_scalars
  from ipykernel import kernelapp as app


tastebud
smoothy
smoothy
tastebud
tastebud
tastebud
smoothy
tastebud
smoothy
tablemate
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
profiterole
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
tastebud
profiterole
tablemate
smoothy
profiterole
profiterole
smoothy
smoothy
profiterole
smoothy
tastebud
profiterole
smoothy
tastebud
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
tastebud
smoothy
smoothy
smoothy
tastebud
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
s

INFO:tensorflow:loss = 0.34320453, step = 201 (0.514 sec)
INFO:tensorflow:global_step/sec: 199.059
INFO:tensorflow:loss = 0.22802089, step = 301 (0.504 sec)
INFO:tensorflow:global_step/sec: 203.006
INFO:tensorflow:loss = 0.25844598, step = 401 (0.490 sec)
INFO:tensorflow:global_step/sec: 202.716
INFO:tensorflow:loss = 0.28230274, step = 501 (0.496 sec)
INFO:tensorflow:global_step/sec: 206.088
INFO:tensorflow:loss = 0.29511085, step = 601 (0.485 sec)
INFO:tensorflow:global_step/sec: 200.392
INFO:tensorflow:loss = 0.2933123, step = 701 (0.498 sec)
INFO:tensorflow:global_step/sec: 202.54
INFO:tensorflow:loss = 0.29490736, step = 801 (0.496 sec)
INFO:tensorflow:global_step/sec: 205.134
INFO:tensorflow:loss = 0.08315605, step = 901 (0.488 sec)
INFO:tensorflow:global_step/sec: 202.573
INFO:tensorflow:loss = 0.2678278, step = 1001 (0.493 sec)
INFO:tensorflow:global_step/sec: 202.949
INFO:tensorflow:loss = 0.45066288, step = 1101 (0.494 sec)
INFO:tensorflow:global_step/sec: 195.129
INFO:tensor

INFO:tensorflow:Finished evaluation at 2018-08-05-18:26:00
INFO:tensorflow:Saving dict for global step 4000: accuracy = 0.8967102, cross_entropy_loss = 0.25321165, global_step = 4000, loss = 0.25321165, precision = 0.9201521, recall = 0.94544876
Accuracy on test set: 89.67%
Recall on test set: 94.54%
precision on test set: 92.02%
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
tastebud
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
tastebud
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
tastebud
cruller
smoothy

smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
profiterole
tastebud
tastebud
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
tastebud
tastebud
tastebud
smoothy
smoothy
smoothy
profiterole
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
profiterole
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
tastebud
smoothy
sm

INFO:tensorflow:global_step/sec: 170.122
INFO:tensorflow:loss = 0.44331506, step = 8901 (0.587 sec)
INFO:tensorflow:global_step/sec: 174.769
INFO:tensorflow:loss = 0.28518933, step = 9001 (0.571 sec)
INFO:tensorflow:global_step/sec: 168.996
INFO:tensorflow:loss = 0.25613967, step = 9101 (0.591 sec)
INFO:tensorflow:global_step/sec: 172.724
INFO:tensorflow:loss = 0.14669077, step = 9201 (0.581 sec)
INFO:tensorflow:global_step/sec: 174.344
INFO:tensorflow:loss = 0.36132538, step = 9301 (0.574 sec)
INFO:tensorflow:global_step/sec: 171.732
INFO:tensorflow:loss = 0.14136067, step = 9401 (0.580 sec)
INFO:tensorflow:global_step/sec: 169.778
INFO:tensorflow:loss = 0.21939448, step = 9501 (0.591 sec)
INFO:tensorflow:global_step/sec: 166.538
INFO:tensorflow:loss = 0.14050384, step = 9601 (0.598 sec)
INFO:tensorflow:global_step/sec: 169.473
INFO:tensorflow:loss = 0.27042985, step = 9701 (0.590 sec)
INFO:tensorflow:global_step/sec: 170.352
INFO:tensorflow:loss = 0.26271117, step = 9801 (0.587 sec)


smoothy
tastebud
smoothy
tablemate
tastebud
smoothy
wisconsinite
tastebud
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
tablemate
smoothy
michigander
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
cruller
cruller
tastebud
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
tastebud
smoothy
smoothy
smoothy
tastebud
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
michigander
tastebud
smoothy
smoothy
tastebud
tastebud
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
cruller
smoothy
smoothy
smoothy
smoothy
profiterole
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
smoothy
smoothy
smoothy
tastebud
smoothy
INFO:tensorflow

INFO:tensorflow:Finished evaluation at 2018-08-05-19:29:56
INFO:tensorflow:Saving dict for global step 12970: accuracy = 0.8975183, cross_entropy_loss = 0.26010302, global_step = 12970, loss = 0.26010302, precision = 0.9337197, recall = 0.93052816
Accuracy on test set: 89.75%
Recall on test set: 93.05%
precision on test set: 93.37%


In [16]:
predictions=model.predict(input_fn=test_input_fn)


# Baseline Neural BOW

In [25]:
from GloveVectors import models; reload(models)

x, y = X_train, y_train
batch_size = 50

#Use Countvectorizer to utilize its built in stop word feature and min document frequency functionality

# vocab=CountVectorizer(stop_words='english', min_df=5, ngram_range=(1, 1))
# vocab.fit_transform(X_train)
# words=vocab.get_feature_names()


# Specify model hyperparameters as used by model_fn


model_params = dict(V=hands.vocab.size, embed_dim=300, hidden_dims=[300,150,75], num_classes=2,
                    encoder_type='bow',
                    lr=0.01, optimizer='adam', beta=0.01,dropout_rate=0.01)
model_fn = models.classifier_model_fn

#STORING TEST DATA INTO ITS OWN VARIABLE

testx, testy = X_test, y_test

testreview=pd.DataFrame(testx)['text']
tokens=testreview.map(tokenizer.tokenize).map(canonicalize)
inp = pd.DataFrame(tokens.values)[0].map(lambda x:double(x,wordset=words))


inp_no_nans=pd.DataFrame({'col1':inp.values,'col2':testy}).dropna()

test_input_fn =  tf.estimator.inputs.numpy_input_fn(
              x={"ids": np.vstack(inp_no_nans.col1.values)},
    y=np.squeeze(pd.DataFrame(inp_no_nans.col2).values),shuffle=False)


    
# RUNNING NEURAL NETWORK


# Clear old log directory
shutil.rmtree(TF_SAVEDIR, ignore_errors=True)

if not os.path.isdir(TF_SAVEDIR):
    os.makedirs(TF_SAVEDIR)
    
with tf.Graph().as_default(), tf.Session() as sess:
    ##
    # Construct the graph here. No session.run calls - just wiring up Tensors.
    ##
    # Add placeholders so we can feed in data.
    x_ph_  = tf.placeholder(tf.float32, shape=[None,model_params['embed_dim']])  # [batch_size x embedding size]
    y_ph_  = tf.placeholder(tf.int32, shape=[None])              # [batch_size]
    
    # Construct the graph using model_fn
    features = {"ids": x_ph_,"hands":hands}  # note that values are Tensors
    estimator_spec = model_fn(features, labels=y_ph_, mode=tf.estimator.ModeKeys.TRAIN,
                              params=model_params)
    loss_     = estimator_spec.loss
    train_op_ = estimator_spec.train_op
    
    ##
    # Done constructing the graph, now we can make session.run calls.
    ##
    sess.run(tf.global_variables_initializer())
    saver = tf.train.Saver()
    
    # Run a single epoch
    t0 = time.time()
    model = tf.estimator.Estimator(model_fn=models.classifier_model_fn, 
           params=model_params,model_dir=trained_filename
           )
    iter=0
    for (bx, by) in utils.multi_batch_generator(100000, x, y):
        # feed NumPy arrays into the placeholder Tensors
        batchreview=pd.DataFrame(bx)['text']
        tokens=batchreview.map(tokenizer.tokenize).map(canonicalize)
        inp = pd.DataFrame(tokens.values)[0].map(lambda x:double(x,wordset=words))
        
        inp_no_nans=pd.DataFrame({'col1':inp.values,'col2':by}).dropna()

        train_input_fn = tf.estimator.inputs.numpy_input_fn(
                        x={"ids":  np.vstack(inp_no_nans.col1.values)},
                        y=np.squeeze(pd.DataFrame(inp_no_nans.col2).values),
                        batch_size=batch_size, num_epochs=1, shuffle=False)
        model.train(input_fn=train_input_fn)
        iter+=1
        if iter%1==0:
#                 model.evaluate(input_fn=train_input_fn)
            saver.save(sess, checkpoint_filename, global_step=iter)
            eval_metrics = model.evaluate(input_fn=test_input_fn, name="test")
            print("Accuracy on test set: {:.02%}".format(eval_metrics['accuracy']))
            print("Recall on test set: {:.02%}".format(eval_metrics['recall']))
            print("precision on test set: {:.02%}".format(eval_metrics['precision']))
#                 print("F1 Score on test set: {:.02%}".format(2*eval_metrics['precision']*eval_metrics['recall']/(eval_metrics['precision']+eval_metrics['recall'])))
            eval_metrics

        
  
    print("Completed one epoch in {:s}".format(utils.pretty_timedelta(since=t0)))
    saver.save(sess, trained_filename)
    
    
    
    #### EVALUATE TEST DATA BELOW###

    testx, testy = X_test, y_test

    testreview=pd.DataFrame(testx)['text']
    tokens=testreview.map(tokenizer.tokenize).map(canonicalize)
    inp = pd.DataFrame(tokens.values)[0].map(lambda x:double(x,wordset=words))
    
    
    inp_no_nans=pd.DataFrame({'col1':inp.values,'col2':testy}).dropna()

    test_input_fn =  tf.estimator.inputs.numpy_input_fn(
                  x={"ids": np.vstack(inp_no_nans.col1.values)},
        y=np.squeeze(pd.DataFrame(inp_no_nans.col2).values),shuffle=False)


    eval_metrics = model.evaluate(input_fn=test_input_fn, name="test")
    print("Accuracy on test set: {:.02%}".format(eval_metrics['accuracy']))
    print("Recall on test set: {:.02%}".format(eval_metrics['recall']))
    print("precision on test set: {:.02%}".format(eval_metrics['precision']))
#     print("F1 Score on test set: {:.02%}".format(2*eval_metrics['precision']*eval_metrics['recall']/(eval_metrics['precision']+eval_metrics['recall'])))
    eval_metrics

/home/younusahmed23/anaconda3/lib/python3.6/site-packages/numpy/core/fromnumeric.py:2957: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/home/younusahmed23/anaconda3/lib/python3.6/site-packages/numpy/core/_methods.py:80: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/w266/yelp_model/Final_Neural_BOW_Trained', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f8986681828>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/w266/yelp_model/Final_N

INFO:tensorflow:global_step/sec: 168.685
INFO:tensorflow:loss = 0.20576888, step = 4801 (0.595 sec)
INFO:tensorflow:global_step/sec: 166.299
INFO:tensorflow:loss = 0.19511695, step = 4901 (0.598 sec)
INFO:tensorflow:global_step/sec: 169.725
INFO:tensorflow:loss = 0.32155564, step = 5001 (0.592 sec)
INFO:tensorflow:global_step/sec: 167.338
INFO:tensorflow:loss = 0.17372881, step = 5101 (0.598 sec)
INFO:tensorflow:global_step/sec: 166.32
INFO:tensorflow:loss = 0.39922607, step = 5201 (0.601 sec)
INFO:tensorflow:global_step/sec: 163.316
INFO:tensorflow:loss = 0.15808322, step = 5301 (0.610 sec)
INFO:tensorflow:global_step/sec: 166.257
INFO:tensorflow:loss = 0.36166248, step = 5401 (0.601 sec)
INFO:tensorflow:global_step/sec: 165.451
INFO:tensorflow:loss = 0.13946147, step = 5501 (0.605 sec)
INFO:tensorflow:global_step/sec: 163.832
INFO:tensorflow:loss = 0.18318617, step = 5601 (0.612 sec)
INFO:tensorflow:global_step/sec: 158.793
INFO:tensorflow:loss = 0.24182346, step = 5701 (0.629 sec)
I

INFO:tensorflow:Saving dict for global step 10000: accuracy = 0.90974426, cross_entropy_loss = 0.22946471, global_step = 10000, loss = 0.22946471, precision = 0.9317384, recall = 0.9502619
Accuracy on test set: 90.97%
Recall on test set: 95.03%
precision on test set: 93.17%
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt-10000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 10001 into /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt.
INFO:tensorflow:loss = 0.18503116, step = 10001
INFO:tensorflow:global_step/sec: 137.525
INFO:tensorflow:loss = 0.33988336, step = 10101 (0.728 sec)
INFO:tensorflow:global_step/sec: 183.175
INFO:tensorflow:loss = 0.27095294, step = 10201 (0.548 sec)
INFO:tensorflow:global_st

In [38]:
predictions=model.predict(input_fn=test_input_fn)

In [40]:
preds=[]
for x in predictions:
    preds.append(x['max'])

INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt-12970
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.


In [45]:
inp_no_nans['col3']=preds

In [54]:
inp_no_nans['col4']=reviews

In [53]:
reviews=[]
for x in inp_no_nans.index:
    reviews.append(testx.loc[x])

In [71]:
inp_no_nans[inp_no_nans['col2']!=inp_no_nans['col3']].loc[488922].col4

"Came here on the suggestion of a cab driver. It was late, and the place I wanted to go to was closed. I had pulled pork mac and cheese, and it was sooo good. I was gonna try the beignets, but I was in the middle of asking the guy behind the counter about them, and he kind of drifted off and forgot to answer me. The inside is very small with about 8 seats and a small air conditioner that won't reach you if you sit by the door. If I ate here again, I'd order to go. 5 stars for the food."

In [39]:
def stemmer(x,wordset=None):
   g=[]
   bad=[]
   for y in x:
       if len(y)>1 and "." not in y and y in wordset:
            bad.append(y)
            try:
                g.append(model2vec[lemmatize(y.strip('.'))])
            except:
                continue
#                 g.append(model2vec[y.strip('.')])
#    return [hands.vocab.word_to_id[y.strip('.')] for y in x if len(y)>1]
   return np.mean(g,axis=0)

   

#  Porter  Stemmer with baseline

In [42]:
from GloveVectors import models; reload(models)

x, y = X_train, y_train
batch_size = 50

#Use Countvectorizer to utilize its built in stop word feature and min document frequency functionality

# vocab=CountVectorizer(stop_words='english', min_df=5, ngram_range=(1, 1))
# vocab.fit_transform(X_train)
# words=vocab.get_feature_names()


# Specify model hyperparameters as used by model_fn


model_params = dict(V=len(model2vec.vocab), embed_dim=300, hidden_dims=[300,150,75], num_classes=2,
                    encoder_type='bow',
                    lr=0.01, optimizer='adam', beta=0.01,dropout_rate=0.01)
model_fn = models.classifier_model_fn

#STORING TEST DATA INTO ITS OWN VARIABLE

# testx, testy = X_test, y_test

# testreview=pd.DataFrame(testx)['text']
# tokens=testreview.map(tokenizer.tokenize).map(canonicalize)
# inp = pd.DataFrame(tokens.values)[0].map(lambda x:stemmer(x,wordset=words))


# inp_no_nans=pd.DataFrame({'col1':inp.values,'col2':testy}).dropna()

# test_input_fn =  tf.estimator.inputs.numpy_input_fn(
#               x={"ids": np.vstack(inp_no_nans.col1.values)},
#     y=np.squeeze(pd.DataFrame(inp_no_nans.col2).values),shuffle=False)


    
# RUNNING NEURAL NETWORK


# Clear old log directory
shutil.rmtree(TF_SAVEDIR, ignore_errors=True)

if not os.path.isdir(TF_SAVEDIR):
    os.makedirs(TF_SAVEDIR)
    
with tf.Graph().as_default(), tf.Session() as sess:
    ##
    # Construct the graph here. No session.run calls - just wiring up Tensors.
    ##
    # Add placeholders so we can feed in data.
    x_ph_  = tf.placeholder(tf.float32, shape=[None,model_params['embed_dim']])  # [batch_size x embedding size]
    y_ph_  = tf.placeholder(tf.int32, shape=[None])              # [batch_size]
    
    # Construct the graph using model_fn
    features = {"ids": x_ph_}  # note that values are Tensors
    estimator_spec = model_fn(features, labels=y_ph_, mode=tf.estimator.ModeKeys.TRAIN,
                              params=model_params)
    loss_     = estimator_spec.loss
    train_op_ = estimator_spec.train_op
    
    ##
    # Done constructing the graph, now we can make session.run calls.
    ##
    sess.run(tf.global_variables_initializer())
    saver = tf.train.Saver()
    
    # Run a single epoch
    t0 = time.time()
    model = tf.estimator.Estimator(model_fn=models.classifier_model_fn, 
           params=model_params,model_dir=trained_filename
           )
    iter=0
    for (bx, by) in utils.multi_batch_generator(100000, x, y):
        # feed NumPy arrays into the placeholder Tensors
        batchreview=pd.DataFrame(bx)['text']
        tokens=batchreview.map(tokenizer.tokenize).map(canonicalize)
        inp = pd.DataFrame(tokens.values)[0].map(lambda x:stemmer(x,wordset=words))

        inp_no_nans=pd.DataFrame({'col1':inp.values,'col2':by}).dropna()

        train_input_fn = tf.estimator.inputs.numpy_input_fn(
                        x={"ids":  np.vstack(inp_no_nans.col1.values)},
                        y=np.squeeze(pd.DataFrame(inp_no_nans.col2).values),
                        batch_size=batch_size, num_epochs=10, shuffle=False)
        model.train(input_fn=train_input_fn)
        iter+=1
        if iter%100==0:
#                 model.evaluate(input_fn=train_input_fn)
            saver.save(sess, checkpoint_filename, global_step=iter)
            eval_metrics = model.evaluate(input_fn=test_input_fn, name="test")
            print("Accuracy on test set: {:.02%}".format(eval_metrics['accuracy']))
            print("Recall on test set: {:.02%}".format(eval_metrics['recall']))
            print("precision on test set: {:.02%}".format(eval_metrics['precision']))
#                 print("F1 Score on test set: {:.02%}".format(2*eval_metrics['precision']*eval_metrics['recall']/(eval_metrics['precision']+eval_metrics['recall'])))
            eval_metrics
            predictions=model.predict(input_fn=test_input_fn)

        
  
    print("Completed one epoch in {:s}".format(utils.pretty_timedelta(since=t0)))
    saver.save(sess, trained_filename)
    
    
    
    #### EVALUATE TEST DATA BELOW###

    testx, testy = X_test, y_test

    testreview=pd.DataFrame(testx)['text']
    tokens=testreview.map(tokenizer.tokenize).map(canonicalize)
    inp = pd.DataFrame(tokens.values)[0].map(lambda x:stemmer(x,wordset=words))
    
    
    inp_no_nans=pd.DataFrame({'col1':inp.values,'col2':testy}).dropna()

    test_input_fn =  tf.estimator.inputs.numpy_input_fn(
                  x={"ids": np.vstack(inp_no_nans.col1.values)},
        y=np.squeeze(pd.DataFrame(inp_no_nans.col2).values),shuffle=True)


    eval_metrics = model.evaluate(input_fn=test_input_fn, name="test")
    print("Accuracy on test set: {:.02%}".format(eval_metrics['accuracy']))
    print("Recall on test set: {:.02%}".format(eval_metrics['recall']))
    print("precision on test set: {:.02%}".format(eval_metrics['precision']))
#     print("F1 Score on test set: {:.02%}".format(2*eval_metrics['precision']*eval_metrics['recall']/(eval_metrics['precision']+eval_metrics['recall'])))
    eval_metrics
    predictions=model.predict(input_fn=test_input_fn)

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/w266/yelp_model/Final_Neural_BOW_Trained', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f99e39ab898>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


/home/younusahmed23/anaconda3/lib/python3.6/site-packages/numpy/core/fromnumeric.py:2957: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/home/younusahmed23/anaconda3/lib/python3.6/site-packages/numpy/core/_methods.py:80: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt.
INFO:tensorflow:loss = 0.7225585, step = 1
INFO:tensorflow:global_step/sec: 190.269
INFO:tensorflow:loss = 0.26323614, step = 101 (0.527 sec)
INFO:tensorflow:global_step/sec: 246.612
INFO:tensorflow:loss = 0.32425967, step = 201 (0.405 sec)
INFO:tensorflow:global_step/sec: 240.723
INFO:tensorflow:loss = 0.19937985, step = 301 (0.416 sec)
INFO:tensorflow:global_step/sec: 247.532
INFO:tensorflow:loss = 0.30222064, step = 401 (0.404 sec)
INFO:tensorflow:global_step/sec: 243.639
INFO:tensorflow:loss = 0.27638632, step = 501 (0.410 sec)
INFO:tensorflow:global_step/sec: 252.331
INFO:tensorflow:loss = 0.20406753, step = 601 (0.396 sec)
INFO:tensorflow:global

INFO:tensorflow:loss = 0.1418715, step = 7901 (0.408 sec)
INFO:tensorflow:global_step/sec: 241.865
INFO:tensorflow:loss = 0.16263902, step = 8001 (0.413 sec)
INFO:tensorflow:global_step/sec: 244.246
INFO:tensorflow:loss = 0.16306075, step = 8101 (0.409 sec)
INFO:tensorflow:global_step/sec: 237.969
INFO:tensorflow:loss = 0.31491908, step = 8201 (0.420 sec)
INFO:tensorflow:global_step/sec: 241.663
INFO:tensorflow:loss = 0.06987072, step = 8301 (0.414 sec)
INFO:tensorflow:global_step/sec: 234.325
INFO:tensorflow:loss = 0.21809109, step = 8401 (0.427 sec)
INFO:tensorflow:global_step/sec: 241.476
INFO:tensorflow:loss = 0.22174405, step = 8501 (0.414 sec)
INFO:tensorflow:global_step/sec: 236.215
INFO:tensorflow:loss = 0.19576228, step = 8601 (0.424 sec)
INFO:tensorflow:global_step/sec: 235.868
INFO:tensorflow:loss = 0.19944231, step = 8701 (0.424 sec)
INFO:tensorflow:global_step/sec: 232.386
INFO:tensorflow:loss = 0.14739746, step = 8801 (0.430 sec)
INFO:tensorflow:global_step/sec: 244.722
I

INFO:tensorflow:global_step/sec: 238.506
INFO:tensorflow:loss = 0.120527446, step = 16101 (0.419 sec)
INFO:tensorflow:global_step/sec: 240.709
INFO:tensorflow:loss = 0.24576405, step = 16201 (0.416 sec)
INFO:tensorflow:global_step/sec: 236.893
INFO:tensorflow:loss = 0.108482644, step = 16301 (0.422 sec)
INFO:tensorflow:global_step/sec: 230.233
INFO:tensorflow:loss = 0.1404098, step = 16401 (0.435 sec)
INFO:tensorflow:global_step/sec: 236.328
INFO:tensorflow:loss = 0.12879114, step = 16501 (0.423 sec)
INFO:tensorflow:global_step/sec: 243.236
INFO:tensorflow:loss = 0.13656327, step = 16601 (0.412 sec)
INFO:tensorflow:global_step/sec: 236.974
INFO:tensorflow:loss = 0.17747396, step = 16701 (0.422 sec)
INFO:tensorflow:global_step/sec: 235.513
INFO:tensorflow:loss = 0.23128892, step = 16801 (0.425 sec)
INFO:tensorflow:global_step/sec: 241.179
INFO:tensorflow:loss = 0.20265609, step = 16901 (0.415 sec)
INFO:tensorflow:global_step/sec: 237.204
INFO:tensorflow:loss = 0.05642876, step = 17001 (

...

INFO:tensorflow:global_step/sec: 309.283
INFO:tensorflow:loss = 0.12120417, step = 95496 (0.323 sec)
INFO:tensorflow:global_step/sec: 311.106
INFO:tensorflow:loss = 0.192148, step = 95596 (0.322 sec)
INFO:tensorflow:global_step/sec: 300.406
INFO:tensorflow:loss = 0.24822792, step = 95696 (0.333 sec)
INFO:tensorflow:global_step/sec: 281.278
INFO:tensorflow:loss = 0.2743605, step = 95796 (0.355 sec)
INFO:tensorflow:global_step/sec: 270.187
INFO:tensorflow:loss = 0.13990808, step = 95896 (0.370 sec)
INFO:tensorflow:global_step/sec: 266.104
INFO:tensorflow:loss = 0.17759877, step = 95996 (0.376 sec)
INFO:tensorflow:global_step/sec: 272.315
INFO:tensorflow:loss = 0.16515015, step = 96096 (0.367 sec)
INFO:tensorflow:global_step/sec: 267.648
INFO:tensorflow:loss = 0.18737096, step = 96196 (0.374 sec)
INFO:tensorflow:global_step/sec: 266.35
INFO:tensorflow:loss = 0.121894486, step = 96296 (0.375 sec)
INFO:tensorflow:global_step/sec: 256.749
INFO:tensorflow:loss = 0.16226357, step = 96396 (0.39

INFO:tensorflow:global_step/sec: 242.265
INFO:tensorflow:loss = 0.24774638, step = 103095 (0.413 sec)
INFO:tensorflow:global_step/sec: 241.377
INFO:tensorflow:loss = 0.14653037, step = 103195 (0.414 sec)
INFO:tensorflow:global_step/sec: 291.809
INFO:tensorflow:loss = 0.26293942, step = 103295 (0.343 sec)
INFO:tensorflow:global_step/sec: 269.282
INFO:tensorflow:loss = 0.14009, step = 103395 (0.372 sec)
INFO:tensorflow:global_step/sec: 248.04
INFO:tensorflow:loss = 0.11229559, step = 103495 (0.403 sec)
INFO:tensorflow:global_step/sec: 260.189
INFO:tensorflow:loss = 0.13034207, step = 103595 (0.384 sec)
INFO:tensorflow:global_step/sec: 247.546
INFO:tensorflow:loss = 0.19015135, step = 103695 (0.404 sec)
INFO:tensorflow:global_step/sec: 245.143
INFO:tensorflow:loss = 0.19713578, step = 103795 (0.408 sec)
INFO:tensorflow:global_step/sec: 238.603
INFO:tensorflow:loss = 0.18452826, step = 103895 (0.419 sec)
INFO:tensorflow:global_step/sec: 239.958
INFO:tensorflow:loss = 0.07916945, step = 103

INFO:tensorflow:global_step/sec: 265.811
INFO:tensorflow:loss = 0.12331346, step = 111195 (0.377 sec)
INFO:tensorflow:global_step/sec: 277.572
INFO:tensorflow:loss = 0.25721863, step = 111295 (0.360 sec)
INFO:tensorflow:global_step/sec: 263.184
INFO:tensorflow:loss = 0.06790879, step = 111395 (0.380 sec)
INFO:tensorflow:global_step/sec: 249.186
INFO:tensorflow:loss = 0.13413574, step = 111495 (0.401 sec)
INFO:tensorflow:global_step/sec: 261.044
INFO:tensorflow:loss = 0.3552292, step = 111595 (0.383 sec)
INFO:tensorflow:global_step/sec: 255.328
INFO:tensorflow:loss = 0.1281285, step = 111695 (0.391 sec)
INFO:tensorflow:global_step/sec: 261.319
INFO:tensorflow:loss = 0.30469653, step = 111795 (0.383 sec)
INFO:tensorflow:global_step/sec: 250.274
INFO:tensorflow:loss = 0.17704153, step = 111895 (0.399 sec)
INFO:tensorflow:global_step/sec: 248.568
INFO:tensorflow:loss = 0.13438523, step = 111995 (0.402 sec)
INFO:tensorflow:global_step/sec: 255.313
INFO:tensorflow:loss = 0.17848143, step = 1

INFO:tensorflow:global_step/sec: 284.557
INFO:tensorflow:loss = 0.22761078, step = 119295 (0.352 sec)
INFO:tensorflow:global_step/sec: 276.723
INFO:tensorflow:loss = 0.038284756, step = 119395 (0.361 sec)
INFO:tensorflow:global_step/sec: 258.307
INFO:tensorflow:loss = 0.1611938, step = 119495 (0.387 sec)
INFO:tensorflow:global_step/sec: 247.755
INFO:tensorflow:loss = 0.5189113, step = 119595 (0.403 sec)
INFO:tensorflow:global_step/sec: 251.374
INFO:tensorflow:loss = 0.13103752, step = 119695 (0.398 sec)
INFO:tensorflow:global_step/sec: 248.723
INFO:tensorflow:loss = 0.34876493, step = 119795 (0.402 sec)
INFO:tensorflow:global_step/sec: 261.821
INFO:tensorflow:loss = 0.10678632, step = 119895 (0.382 sec)
INFO:tensorflow:Saving checkpoints for 119993 into /tmp/w266/yelp_model/Final_Neural_BOW_Trained/model.ckpt.
INFO:tensorflow:Loss for final step: 0.11218847.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorf

INFO:tensorflow:loss = 0.09074282, step = 126794 (0.387 sec)
INFO:tensorflow:global_step/sec: 257.611
INFO:tensorflow:loss = 0.27387387, step = 126894 (0.388 sec)
INFO:tensorflow:global_step/sec: 263.434
INFO:tensorflow:loss = 0.3033484, step = 126994 (0.379 sec)
INFO:tensorflow:global_step/sec: 249.546
INFO:tensorflow:loss = 0.09323755, step = 127094 (0.401 sec)
INFO:tensorflow:global_step/sec: 246.341
INFO:tensorflow:loss = 0.12360555, step = 127194 (0.406 sec)
INFO:tensorflow:global_step/sec: 254.739
INFO:tensorflow:loss = 0.14405583, step = 127294 (0.392 sec)
INFO:tensorflow:global_step/sec: 246.786
INFO:tensorflow:loss = 0.2074197, step = 127394 (0.405 sec)
INFO:tensorflow:global_step/sec: 252.902
INFO:tensorflow:loss = 0.14294523, step = 127494 (0.396 sec)
INFO:tensorflow:global_step/sec: 255.434
INFO:tensorflow:loss = 0.17493469, step = 127594 (0.391 sec)
INFO:tensorflow:global_step/sec: 250.313
INFO:tensorflow:loss = 0.50745565, step = 127694 (0.399 sec)
INFO:tensorflow:global_